In [ ]:
# better formatting for large floats
import pandas as pd
pd.options.display.float_format = "{:,.2f}".format
from ipywidgets import widgets
import os
os.environ["SERENITAS_APP_NAME"] = "notebook"

In [ ]:
from risk.swaptions import get_swaption_portfolio
import datetime
from serenitas.analytics.base import Trade
from serenitas.utils.pool import dawn_pool
from serenitas.analytics.option import BlackSwaption
value_date = datetime.date.today()
Trade.init_ontr(value_date)
BlackSwaption.clear_cache()

In [ ]:
with dawn_pool.connection() as conn:
    portf = get_swaption_portfolio(value_date, conn)
portf.index_formatter = lambda t: (t[2], t[1])
df = portf._todf().dropna(axis=1, how="all")
df.index.names = ["fund", "trade_id"]
df = df.reset_index()
df = df.set_index(["Expiry", "Desc", "Strike", "fund"]).sort_index()
df

In [ ]:
greeks = df.assign(Delta=lambda df: df.Delta * df.Notional, Gamma=lambda df: df.Gamma * df.Notional).groupby(["Desc", "fund"], group_keys=False)[["Delta", "Gamma"]].sum()

In [ ]:
hedges = {}
with dawn_pool.connection() as conn:
    for fund in ["SERCGMAST", "BOWDST", "ISOSEL"]:
        hedges[fund] = pd.read_sql_query("SELECT security_desc, notional FROM list_cds_positions_by_strat(%s, %s) "
                                         "WHERE folder in ('IGOPTDEL', 'HYOPTDEL')",
                                         conn, params=(value_date, fund))
hedges = pd.concat(hedges, names=["fund"])
hedges = hedges.groupby(["security_desc", "fund"]).sum()
def f(s):
    l = s.split(" ")
    return f"{l[1]}{l[3][1:]} {l[4].lower()}r"

hedges = hedges.reset_index("security_desc")
hedges["security_desc"] = hedges["security_desc"].apply(f)
hedges = hedges.rename(columns={"notional": "current hedge", "security_desc": "Desc"}).set_index("Desc", append=True).swaplevel()
risk = pd.concat([hedges, greeks], axis=1)
risk = risk.assign(net_delta=risk["current hedge"] + risk.Delta)
risk.swaplevel().sort_index()

In [ ]:
portf._todf().groupby(level=0)[["Theta"]].sum()

In [ ]:
import numpy as np
sr = np.linspace(65, 80, 100)
rec= []
for s in sr:
    delta = 0.
    gamma = 0.
    for t in portf.trades:
        if t.index.index_type == "IG":
            t.index.mark(ref=s)
            delta += t.delta * t.notional
            gamma += t.gamma
    rec.append((s, gamma, delta))
df = pd.DataFrame.from_records(rec, columns=['spread', 'gamma', 'delta'])
df = df.set_index('spread')
df.delta += risk.loc['IG37 5yr', 'current hedge']

In [ ]:
from matplotlib import pyplot as plt
def get_newaxes(num):
    plt.close(num)
    fix, axes = plt.subplots(figsize=(10,5), num=num)
    return axes

axes = get_newaxes(1)
df.delta.plot(ax=axes)

In [ ]:
axes = get_newaxes(2)
df.gamma.plot(ax=axes)

In [ ]:
portf.pv

# 